In [ ]:
import numpy as np
import scipy.linalg as la
import matplotlib.pyplot as plt

## Sistemas lineales de ecuaciones diferenciales ordinarias y con coeficientes constantes

El siguiente sistema de ecuaciones diferenciales con coeficientes constantes:

$${\displaystyle {\frac {dx}{dt}}=3x-4y,\quad {\frac {dy}{dt}}=4x-7y}$$

se puede escribir en forma matricial:

$$
{\displaystyle {\begin{pmatrix}x'\\y'\end{pmatrix}}={\begin{pmatrix}3&-4\\4&-7\end{pmatrix}}{\begin{pmatrix}x\\y\end{pmatrix}}}
$$

Si además escribimos $\mathbf{v}$ para el vector
$$
\mathbf{v} = {\begin{pmatrix}x\\y\end{pmatrix}}
$$
el sistema se escribe
$$
\dot{\mathbf{v}} = A \cdot\mathbf{v}
$$
y la solución general del problema es de la forma
$$
\mathbf{v} = \exp\left(tA\right)\cdot\mathbf{v}_0
$$
donde
$$
\mathbf{v}_0=\mathbf{v}(t=0)
$$
es el valor inicial.

## Problema de valores iniciales

Vamos a usar los cálculos anteriores para obtener la solución del sistema con dato inicial

$$
\mathbf{v}_0={\begin{pmatrix}1\\1\end{pmatrix}}
$$

Para calcular la exponencial de la matriz $At$, usaremos la diagonalización de $A$, pero no calculamos la diagonalización para cada valor de $t$, sino que diagonalizamos $A$ _una sóla vez_
$$
A = P\cdot D \cdot P^{-1}
$$

y usamos la fórmula:

$$\exp(tA)
= P\cdot 
\left(\begin{array}{cc}
  e^{t d_1} &  0\\
  0 & e^{t d_2}
\end{array}\right)
\cdot P^{-1}
$$


In [ ]:
A = np.array([[3, -4], [4, -7]])
v0 = np.array([1,1])

In [ ]:
avals, avecs = np.linalg.eig(A)
P = avecs
D = np.diag(avals)
Pinv = la.inv(P)
print(D)
P@D@Pinv

In [ ]:
def expAt(t):
    #Recuerda que np.diag (al igual que diag en matlab) tiene dos usos
    # 1. Construir una matriz diagonal a partir de una lista o array 1D
    # 2. Extraer la diagonal de una matriz cuadrada
    expDt = np.diag([np.exp(d*t) for d in np.diag(D)])
#    expDt = np.exp(t*np.diag(D)) #tambien funciona
    return P@expDt@Pinv

In [ ]:
# Comprobamos que exp(A)@exp(-A) = identidad (salvo error numérico)
expAt(1)@expAt(-1)

In [ ]:
# Comprobamos que exp(2A)=exp(A)@exp(A) (salvo error numérico)
expAt(2) - expAt(1)@expAt(1)

Dibujamos las soluciones: la gráfica muestra la evolución de $x(t)$ e $y(t)$ como funciones del tiempo, para tiempo $t$ entre $0$ y $2$:

In [ ]:
t0, tf = 0, 2
ntimes = 200
ts = np.linspace(t0, tf, ntimes)
ys = np.zeros((2,ntimes))
for j in range(ntimes):
    tj = ts[j]
    ys[:,j] = expAt(tj)@v0
    
plt.plot(ts, ys[0,:], label='x')
plt.plot(ts, ys[1,:], label='y')
plt.xlabel('t')
plt.legend()

### Ejercicio: péndulo lineal

Escribe la ecuación de segundo orden del péndulo lineal sin rozamiento como un sistema de ecuaciones:
$$
m \cdot l\cdot \theta''+m \cdot g \cdot \theta=0
$$
encuentra la solución por el método anterior, y dibuja las trayectorias solución del problema de valor inicial para la ecuación anterior para $l=10$ (metros), $m=20$ (kg), $g$ la aceleración de la gravedad, y con dato inicial
$$
\theta(0)=\pi/2,\; \theta'(0)=0
$$

 - **Atención**: al diagonalizar la matriz de coeficientes aparecerán autovalores complejos: ¿es grave, doctor?

### Ejercicio: péndulo lineal con rozamiento

Añadimos ahora un término de rozamiento:
$$
m \cdot l\cdot \theta''+k \cdot l\cdot \theta'+m \cdot g \cdot \theta=0
$$

encuentra la solución por el método anterior, y dibuja las trayectorias solución del problema de valor inicial para la ecuación anterior para $k=4$ (kg/s), $l=10$ (m), $m=20$ (kg), $g$ la aceleración de la gravedad, y el mismo dato inicial de antes:
$$
\theta(0)=\pi/2,\; \theta'(0)=0
$$

## Diagrama de fases

Un sistema de ecuaciones diferenciales
$$
\frac {d\mathbf{y}}{dt} = f(t, \mathbf{y})
$$
se llama _sistema autónomo_ cuando $f$ no depende del tiempo.

Para sistemas autónomos con dos incógnitas $x$ e $y$, es muy iluminador estudiar cómo un _estado del sistema_ $(x_0,y_0)$ evoluciona bajo el sistema de ecuaciones en un **plano de fases** con ejes $x$ e $y$.

Para ello, dibujamos unas cuantas trayectorias, para distintos valores iniciales, y observamos si $x$ e $y$ crecen, decrecen, oscilan, convergen a un valor de equilibrio, etc.

In [ ]:
A = np.array([[-1, 0], [0, -3]])
avals, avecs = np.linalg.eig(A)
P = avecs
D = np.diag(avals)
Pinv = la.inv(P)

def expAt(t):
    #Recuerda que np.diag (al igual que diag en matlab) tiene dos usos
    # 1. Construir una matriz diagonal a partir de una lista o array 1D
    # 2. Extraer la diagonal de una matriz cuadrada
    expDt = np.diag([np.exp(d*t) for d in np.diag(D)])
    return P@expDt@Pinv

In [ ]:
t0, tf = 0, 4
ntimes = 200
ts = np.linspace(t0, tf, ntimes)
condiciones_iniciales = [(np.sin(theta), np.cos(theta)) for theta in np.linspace(0,2*np.pi,14)]
for v0 in condiciones_iniciales:
    ys = np.zeros((2,ntimes))
    plt.plot(v0[0], v0[1], 'ok')
    for j in range(ntimes):
        tj = ts[j]
        ys[:,j] = expAt(tj)@v0

    plt.plot(ys[0,:], ys[1,:])

plt.ylim( (-2,2) )
plt.xlim( (-2,2) )
plt.xlabel('x')
plt.ylabel('y')
plt.axvline()
plt.axhline()

### Ejercicio: diagrama de fases del péndulo lineal

Dibuja un diagrama de fases del péndulo lineal sin rozamiento que estudiamos antes, para varias condiciones iniciales con distinto ángulo inicial pero velocidad inicial $\theta' = 0$.



### Ejercicio: diagrama de fases del péndulo lineal

Repite el ejercicio anterior, para varias condiciones iniciales con ángulo inicial $\theta=0$ pero distintas velocidades iniciales.



### Ejercicio: diagrama de fases del péndulo lineal con rozamiento

Repite los dos ejercicios anteriores, pero para un péndulo con rozamiento $k=4$ (kg/s).



## Comprobación con el método de Euler

Puedes comprobar las soluciones usando el "método de Euler". Aunque es parte del temario de Cálculo III, lo estudiaremos con detalle más adelante en esta asignatura. Por ahora _sólo queremos aproximar la solución por otro método diferente_. Se trata de reemplazar las funciones $(x(t), y(t))$, solución del sistema de ecuaciones:

$${\displaystyle {\frac {dx}{dt}}=3x-4y,\quad {\frac {dy}{dt}}=4x-7y}$$

por una serie de valores discretos 
$$x_0= x(t_0), x_1\approx x(t_1), \dots, x_n\approx x(t_n),$$
$$y_0= y(t_0), y_1\approx y(t_1), \dots, y_n\approx y(t_n)$$ 
en tiempos
$$t_0, t_1, \dots, t_n$$
equiespaciados (es decir, $t_{j+1} - t_j$ es constante, igual a $h>0$).

La regla es:
$$x_{j+1} = x_j + h (3x_j-4y_j)\quad
y_{j+1} = y_j + h (4x_j-7y_j)
$$

In [ ]:
def euler(f, y0, t0, tf, N):
    'método de Euler'
    h = (tf - t0)/N
    ts = np.linspace(t0, tf, N+1)
    tj = 0
    #admitimos que el argumento y0 sea "list", pero lo convertimos a array
    yj = np.array(y0)
    d = yj.shape[0]
    ys = np.zeros((d,N+1))
    for j in range(N+1):
        ys[:,j] = yj
        yj = yj + h*f(tj, yj)
        tj = tj + h
    return ts, ys

Para llamar a este método (y a otros más sofisticados) es necesario escribir el sistema de ecuaciones diferenciales en la forma:

$$
\frac {d\mathbf{y}}{dt} = f(t, \mathbf{y})
$$

In [ ]:
v0 = np.array([1,1])

def f(t, ys):
    x,y = ys
    return np.array([3*x-4*y,4*x-7*y])

In [ ]:
t0, tf = 0, 2
ntimes = 200

ts, ys = euler(f, v0, t0, tf, ntimes)

plt.plot(ts, ys[0,:], label='x')
plt.plot(ts, ys[1,:], label='y')
plt.xlabel('t')
plt.legend()